In [ ]:
from datetime import datetime
import time as tm
import warnings
warnings.filterwarnings("ignore")
import shutil
import os
import pandas as pd
import matplotlib
matplotlib.use(u'nbAgg')
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
import pickle
from sklearn.manifold import TSNE
from sklearn import preprocessing
import pandas as pd
from multiprocessing import Process # this is used for multithreading
import multiprocessing
from multiprocessing import Pool
import codecs # this is used for file operations
import random as r
from tqdm import tqdm
from xgboost import XGBClassifier
from sklearn.model_selection import RandomizedSearchCV
from sklearn.tree import DecisionTreeClassifier
from sklearn.calibration import CalibratedClassifierCV
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import log_loss, confusion_matrix, accuracy_score
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier
from sklearn.feature_extraction.text import CountVectorizer
import scipy
from scipy.sparse import csr_matrix
from sklearn.preprocessing import normalize
from sklearn.feature_selection import SelectKBest, chi2
import array
import csv

In [ ]:
#!pip install --upgrade --force-reinstall --no-deps kaggle
from google.colab import files
api_token = files.upload()

Saving kaggle.json to kaggle.json


In [ ]:
!mkdir ~/.kaggle
!cp kaggle.json ~/.kaggle/
!chmod 600 /root/.kaggle/kaggle.json

In [ ]:
os.listdir()

['.config', 'kaggle.json', 'sample_data']

In [ ]:
!kaggle competitions download -c 'malware-classification'

100% 17.5G/17.5G [04:53<00:00, 79.3MB/s]
100% 17.5G/17.5G [04:53<00:00, 64.1MB/s]
100% 17.8G/17.8G [05:14<00:00, 68.3MB/s]
100% 17.8G/17.8G [05:14<00:00, 60.6MB/s]
  0% 0.00/185k [00:00<?, ?B/s]
100% 185k/185k [00:00<00:00, 62.6MB/s]
  0% 0.00/265k [00:00<?, ?B/s]
100% 265k/265k [00:00<00:00, 81.0MB/s]
  0% 0.00/4.06M [00:00<?, ?B/s]
100% 4.06M/4.06M [00:00<00:00, 36.3MB/s]


In [ ]:
# Keep only train.7z, trainLables files remove other files as shown below
!rm test.7z
!rm sampleSubmission.csv.zip
!rm dataSample.7z

In [ ]:
data=!7z l train.7z
print(len(data))
print(type(data))

21759
<class 'IPython.utils.text.SList'>


In [ ]:
byte_file_list=[]
asm_file_list=[]
for i in data:
  if (i.endswith("bytes")):
    byte_file_list.append(i)
  elif (i.endswith("asm")):
    asm_file_list.append(i)

In [ ]:
print('Number of Byte files',len(byte_file_list))

Number of Byte files 10868


In [ ]:
print('Number of ASM files',len(asm_file_list))

Number of ASM files 10868


In [ ]:
os.listdir()

['.config', 'trainLabels.csv', 'kaggle.json', 'train.7z', 'sample_data']

In [ ]:
byte_file_list[0]

'2015-01-29 05:00:00 ....A      5256192               train/01azqd4InC7m9JpocGv5.bytes'

In [ ]:
# Removing extra character and to get only the file name
(byte_file_list[0].split()[-1]).replace('train/', '')

'01azqd4InC7m9JpocGv5.bytes'

In [ ]:
# Doing the same operation for all the files
byte_file_name=[]
for i in range(0,len(byte_file_list)):
  byte_file_name.append(byte_file_list[i].split()[-1].replace('train/', ''))

In [ ]:
byte_file_name[:3]

['01azqd4InC7m9JpocGv5.bytes',
 '01IsoiSMh5gxyDYTl4CB.bytes',
 '01jsnpXSAlgw6aPeDxrU.bytes']

In [ ]:
# Finding only the file names of ASM files and storing the file names in an array
asm_file_name=[]
for i in range(0,len(asm_file_list)):
  asm_file_name.append(asm_file_list[i].split()[-1].replace('train/', ''))

In [ ]:
asm_file_name[:3]

['01azqd4InC7m9JpocGv5.asm',
 '01IsoiSMh5gxyDYTl4CB.asm',
 '01jsnpXSAlgw6aPeDxrU.asm']

In [ ]:
print(len(asm_file_name))

10868


In [ ]:
import os
# Getting the current working directory
os.getcwd()

'/content'

In [ ]:
os.listdir()

['.config', 'trainLabels.csv', 'kaggle.json', 'train.7z', 'sample_data']

In [ ]:
# Downloading only a single byte file from train.7z
%%time
file_name=byte_file_name[0]
!7z e train.7z -o/content *$file_name -r


7-Zip [64] 16.02 : Copyright (c) 1999-2016 Igor Pavlov : 2016-05-21
p7zip Version 16.02 (locale=en_US.UTF-8,Utf16=on,HugeFiles=on,64 bits,2 CPUs Intel(R) Xeon(R) CPU @ 2.00GHz (50653),ASM,AES-NI)

Scanning the drive for archives:
  0M Scan         1 file, 18810691091 bytes (18 GiB)

Extracting archive: train.7z
--
Path = train.7z
Type = 7z
Physical Size = 18810691091
Headers Size = 339764
Method = LZMA:24
Solid = +
Blocks = 94

  0%      1% . train/kQEbWRHa04gOYDqM1NJ6.asm                                       3% . train/kQEbWRHa04gOYDqM1NJ6.asm                                       7% 1 . train/KqEgONxfHdP5lLaBIGQk.asm                                        12% 1 . train/KqEgONxfHdP5lLaBIGQk.asm   

In [ ]:
# Deleting the file
os.remove(file_name)

In [ ]:
print('Completed till now')

Completed till now


In [ ]:
!mkdir bytefiles

In [ ]:
os.listdir()

['.config',
 'trainLabels.csv',
 'kaggle.json',
 'train.7z',
 'bytefiles',
 'sample_data']

In [ ]:
from datetime import datetime
#To download all the byte files from train.7z and below code will take almost 15mins.
start=datetime.now()

!7z e train.7z -o/content/bytefiles *.bytes -r

end=datetime.now()
difference=end-start
print('Time taken to extract all the byte files',difference)


7-Zip [64] 16.02 : Copyright (c) 1999-2016 Igor Pavlov : 2016-05-21
p7zip Version 16.02 (locale=en_US.UTF-8,Utf16=on,HugeFiles=on,64 bits,2 CPUs Intel(R) Xeon(R) CPU @ 2.00GHz (50653),ASM,AES-NI)

Scanning the drive for archives:
  0M Scan         1 file, 18810691091 bytes (18 GiB)

Extracting archive: train.7z
--
Path = train.7z
Type = 7z
Physical Size = 18810691091
Headers Size = 339764
Method = LZMA:24
Solid = +
Blocks = 94

  0%      0% . train/kQEbWRHa04gOYDqM1NJ6.asm                                       0% 1 . train/KqEgONxfHdP5lLaBIGQk.asm                                         0% 2 . train/kqiOdVbRQlB2s907GLMv.asm                                         0% 5 . train/kQsiVxDbAXt23wRWal57.asm

In [ ]:
print('Number of byte files extracted is',len(os.listdir('bytefiles')))

Number of byte files extracted is 10868


In [ ]:
############################################

In [ ]:
#https://www.thepythoncode.com/article/get-directory-size-in-bytes-using-python

def get_directory_size(directory):
    """Returns the `directory` size in bytes."""
    total = 0
    try:
        # print("[+] Getting the size of", directory)
        for entry in os.scandir(directory):
            if entry.is_file():
                # if it's a file, use stat() function
                total += entry.stat().st_size
            elif entry.is_dir():
                # if it's a directory, recursively call this function
                total += get_directory_size(entry.path)
    except NotADirectoryError:
        # if `directory` isn't a directory, get the file size then
        return os.path.getsize(directory)
    except PermissionError:
        # if for whatever reason we can't open the folder, return 0
        return 0
    return total

In [ ]:
def get_size_format(b, factor=1024, suffix="B"):
    """
    Scale bytes to its proper byte format
    e.g:
        1253656 => '1.20MB'
        1253656678 => '1.17GB'
    """
    for unit in ["", "K", "M", "G", "T", "P", "E", "Z"]:
        if b < factor:
            return f"{b:.2f}{unit}{suffix}"
        b /= factor
    return f"{b:.2f}Y{suffix}"

In [ ]:
os.listdir()

['.config',
 'trainLabels.csv',
 'kaggle.json',
 'train.7z',
 'bytefiles',
 'sample_data']

In [ ]:
get_size_format(get_directory_size("bytefiles"))

'47.36GB'

In [ ]:
print('Number of byte files extracted is',len(os.listdir('bytefiles')))

Number of byte files extracted is 10868


In [ ]:
###############################################################

In [ ]:
train_level = pd.read_csv('/content/trainLabels.csv')
train_level.head(10)

Id  Class
0  01kcPWA9K2BOxQeS5Rju      1
1  04EjIdbPV5e1XroFOpiN      1
2  05EeG39MTRrI6VY21DPd      1
3  05rJTUWYAKNegBk2wE8X      1
4  0AnoOZDNbPXIr2MRBSCJ      1
5  0AwWs42SUQ19mI7eDcTC      1
6  0cH8YeO15ZywEhPrJvmj      1
7  0DNVFKwYlcjO7bTfJ5p1      1
8  0DqUX5rkg3IbMY6BLGCE      1
9  0eaNKwluUmkYdIvZ923c      1

In [ ]:
dict_val = {}
for x in range(len(train_level)):
    currentid = train_level.iloc[x,0]
    currentvalue = train_level.iloc[x,1]
    dict_val.setdefault(currentid, list())
    # dict_val[currentid].append(currentvalue)
    dict_val[currentid] = currentvalue

#dict_val

### Feature Extraction from 'bytefiles'

In [ ]:
# list byteFiles directory
files = os.listdir('bytefiles')
print(len(files))
train_files = files[:6500]   # I have used only 6500 files for further processing
print(len(train_files))

10868
6500


In [ ]:
a = "00,01,02,03,04,05,06,07,08,09,0a,0b,0c,0d,0e,0f,10,11,12,13,14,15,16,17,18,19\
,1a,1b,1c,1d,1e,1f,20,21,22,23,24,25,26,27,28,29,2a,2b,2c,2d,2e,2f,30,31,32,33,34,35\
,36,37,38,39,3a,3b,3c,3d,3e,3f,40,41,42,43,44,45,46,47,48,49,4a,4b,4c,4d,4e,4f,50,51\
,52,53,54,55,56,57,58,59,5a,5b,5c,5d,5e,5f,60,61,62,63,64,65,66,67,68,69,6a,6b,6c,6d\
,6e,6f,70,71,72,73,74,75,76,77,78,79,7a,7b,7c,7d,7e,7f,80,81,82,83,84,85,86,87,88,89\
,8a,8b,8c,8d,8e,8f,90,91,92,93,94,95,96,97,98,99,9a,9b,9c,9d,9e,9f,a0,a1,a2,a3,a4,a5\
,a6,a7,a8,a9,aa,ab,ac,ad,ae,af,b0,b1,b2,b3,b4,b5,b6,b7,b8,b9,ba,bb,bc,bd,be,bf,c0,c1\
,c2,c3,c4,c5,c6,c7,c8,c9,ca,cb,cc,cd,ce,cf,d0,d1,d2,d3,d4,d5,d6,d7,d8,d9,da,db,dc,dd\
,de,df,e0,e1,e2,e3,e4,e5,e6,e7,e8,e9,ea,eb,ec,ed,ee,ef,f0,f1,f2,f3,f4,f5,f6,f7,f8,f9,fa,fb,fc,fd,fe,ff,??"
print(len(a))
print(type(a))
li = list(a.split(','))
print(li)
print(len(li))

770
<class 'str'>
['00', '01', '02', '03', '04', '05', '06', '07', '08', '09', '0a', '0b', '0c', '0d', '0e', '0f', '10', '11', '12', '13', '14', '15', '16', '17', '18', '19', '1a', '1b', '1c', '1d', '1e', '1f', '20', '21', '22', '23', '24', '25', '26', '27', '28', '29', '2a', '2b', '2c', '2d', '2e', '2f', '30', '31', '32', '33', '34', '35', '36', '37', '38', '39', '3a', '3b', '3c', '3d', '3e', '3f', '40', '41', '42', '43', '44', '45', '46', '47', '48', '49', '4a', '4b', '4c', '4d', '4e', '4f', '50', '51', '52', '53', '54', '55', '56', '57', '58', '59', '5a', '5b', '5c', '5d', '5e', '5f', '60', '61', '62', '63', '64', '65', '66', '67', '68', '69', '6a', '6b', '6c', '6d', '6e', '6f', '70', '71', '72', '73', '74', '75', '76', '77', '78', '79', '7a', '7b', '7c', '7d', '7e', '7f', '80', '81', '82', '83', '84', '85', '86', '87', '88', '89', '8a', '8b', '8c', '8d', '8e', '8f', '90', '91', '92', '93', '94', '95', '96', '97', '98', '99', '9a', '9b', '9c', '9d', '9e', '9f', 'a0', 'a1', 'a2', 'a3

In [ ]:
bigram_vocab = []
for i in li:
    for j in li:
        bigram_vocab.extend([i + ' ' + j])

In [ ]:
bigram_vocab[:5]

['00 00', '00 01', '00 02', '00 03', '00 04']

In [ ]:
print(len(bigram_vocab))

66049


In [ ]:
import scipy
from scipy.sparse import csr_matrix
from tqdm import tqdm
from sklearn.feature_selection import SelectKBest
import time as tm

class_bytes = []
fnames_ID = []
def bigram_feature(files):
    pid = os.getpid()
    str_pid = str(pid)
    tot = len(files)
    global vect
    vect = CountVectorizer(lowercase=False, vocabulary=bigram_vocab, ngram_range=(2,2))
    bigram_byte_vect = csr_matrix((len(files), len(bigram_vocab)))
    feature_names = vect.get_feature_names()

    for i, file in tqdm(enumerate(files)):
        f = open('bytefiles/' + file)
        text = f.read().replace('\n', ' ').lower()
        file_name = file.split('.')
        fnames_ID.extend(key for key, value in dict_val.items() if file_name[0] == key)
        class_bytes.extend(value for key, value in dict_val.items() if file_name[0] == key)
        print()
        print('File name is :-', file,' Its id is :-', file_name[0],' Corresponding class is:-', class_bytes[i])
        # print('The contents of file', file, 'are :- \n')
        # print(text[:1000])
        bigram_byte_vect[i, :] += (vect.fit_transform([text]))
        f.close()
    return bigram_byte_vect

In [ ]:
start_time = tm.time()
# test_output = list(bigram_feature(test_files))
train_output = bigram_feature(train_files).toarray()
selector = SelectKBest(chi2, k=2200)
top_2000_features = selector.fit_transform(train_output, class_bytes)

# print('Time taken is :- ', tm.time() - start_time, 'seconds')
print('Time taken is :- ', (tm.time() - start_time)/ 3600, 'hours')

1it [00:00,  4.72it/s]


File name is :- 5sLXK39w4fkSzAVi1Q6U.bytes  Its id is :- 5sLXK39w4fkSzAVi1Q6U  Corresponding class is:- 8

File name is :- BAzLufVOT1dQk0yg9X8o.bytes  Its id is :- BAzLufVOT1dQk0yg9X8o  Corresponding class is:- 2


2it [00:03,  1.05s/it]


File name is :- e1oUMvCJ5rNWFnLdPglK.bytes  Its id is :- e1oUMvCJ5rNWFnLdPglK  Corresponding class is:- 3


4it [00:05,  1.07it/s]

...


File name is :- D0CpBFrm82d6aqcvnTLz.bytes  Its id is :- D0CpBFrm82d6aqcvnTLz  Corresponding class is:- 3


6499it [7:07:59,  7.69s/it]


File name is :- 4Eo8QvuZFWCBR6i0rhs7.bytes  Its id is :- 4Eo8QvuZFWCBR6i0rhs7  Corresponding class is:- 7


6500it [7:08:05,  3.95s/it]


Time taken is :-  7.136749272677633 hours


In [ ]:
print(len(train_output))
print(len(class_bytes))

6500
6500


In [ ]:
# https://stackoverflow.com/questions/39839112/the-easiest-way-for-getting-feature-names-after-running-selectkbest-in-scikit-le?answertab=active#tab-top
# feature_names = list(test_output.columns.values)
feature_names = np.asarray(vect.get_feature_names())   # [ch2.get_support()]  # vect.get_feature_names()
# feature_names = vector_names
sel_Bool = selector.get_support()
new_features = [] # The list of your K best features

for bool, feature in zip(sel_Bool, feature_names):
    if bool:
        new_features.append(feature)

# new_features = np.asarray(vect.get_feature_names())[selector.get_support()]  # vect.get_feature_names()
dataframe = pd.DataFrame(top_2000_features, columns=new_features)
dataframe.head()

00 00  00 01   00 02  00 03  00 04  ...  ff 9d  ff 9f  ff a5  ff a6    ff ff
0  26269.0  209.0    95.0   88.0  100.0  ...    0.0    0.0    0.0    0.0   1796.0
1  22910.0  721.0  1056.0   77.0  217.0  ...  233.0  273.0  228.0  184.0  11941.0
2   3237.0   30.0    18.0   41.0   16.0  ...   18.0   15.0   14.0   14.0     71.0
3  16583.0  294.0    71.0   67.0  131.0  ...    1.0    5.0    1.0    0.0   2794.0
4   8345.0  137.0    15.0   17.0   68.0  ...    8.0   14.0    7.0    6.0   1146.0

[5 rows x 2200 columns]

In [ ]:
dataframe.shape

(6500, 2200)

In [ ]:
# selected_df = pd.DataFrame(top_20_features, columns=[test_output.columns[i] for i in range(len(test_output.columns)) if selector.get_support()[i]])
# selected_df = pd.DataFrame(top_20_features, columns=[test_files.columns[i] for i in range(len(test_files.columns)) if selector.get_support()[i]])

In [ ]:
dataframe.to_csv('bigram_features.csv')

In [ ]:
data = pd.read_csv('bigram_features.csv').drop('Unnamed: 0', axis = 1)
data.head()

00 00  00 01   00 02  00 03  00 04  ...  ff 9d  ff 9f  ff a5  ff a6    ff ff
0  26269.0  209.0    95.0   88.0  100.0  ...    0.0    0.0    0.0    0.0   1796.0
1  22910.0  721.0  1056.0   77.0  217.0  ...  233.0  273.0  228.0  184.0  11941.0
2   3237.0   30.0    18.0   41.0   16.0  ...   18.0   15.0   14.0   14.0     71.0
3  16583.0  294.0    71.0   67.0  131.0  ...    1.0    5.0    1.0    0.0   2794.0
4   8345.0  137.0    15.0   17.0   68.0  ...    8.0   14.0    7.0    6.0   1146.0

[5 rows x 2200 columns]

In [ ]:
data.shape

(6500, 2200)

In [ ]:
data.insert(loc=0, column='ID', value=fnames_ID)
data.insert(loc=1, column='Class', value=class_bytes)
data["Class"] = data.Class.astype(float)

In [ ]:
data.shape
data.tail()

ID  Class    00 00  00 01  ...  ff 9f  ff a5  ff a6   ff ff
6495  2TtDCQBqdnV314lNMxSk    3.0   5636.0   44.0  ...   29.0   14.0   14.0   201.0
6496  0wqQj9ngaAVxI4SLr5H7    8.0  15329.0   57.0  ...    0.0    1.0    0.0    72.0
6497  2POsRoLQDjVz89qgSpnY    2.0  17057.0  623.0  ...   69.0  128.0  222.0  5685.0
6498  D0CpBFrm82d6aqcvnTLz    3.0   5473.0   47.0  ...   16.0   30.0   14.0    84.0
6499  4Eo8QvuZFWCBR6i0rhs7    7.0   3632.0   29.0  ...    0.0    0.0    0.0   229.0

[5 rows x 2202 columns]

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
data.head()
data.to_csv('bigram_features.csv')

In [ ]:
!cp bigram_features.csv "drive/My Drive/16. Microsoft Malware Detection"

In [ ]:
# df = pd.read_csv('/content/drive/MyDrive/16. Microsoft Malware Detection/bigram_features.csv').drop('Unnamed: 0', axis = 1)
# df.head()
df = pd.read_csv('/content/drive/MyDrive/16. Microsoft Malware Detection/6500_bigram_feature.csv').drop('Unnamed: 0', axis=1)
df.head()

ID  Class    00 00  00 01  ...  ff 9f  ff a5  ff a6    ff ff
0  5sLXK39w4fkSzAVi1Q6U    8.0  26269.0  209.0  ...    0.0    0.0    0.0   1796.0
1  BAzLufVOT1dQk0yg9X8o    2.0  22910.0  721.0  ...  273.0  228.0  184.0  11941.0
2  e1oUMvCJ5rNWFnLdPglK    3.0   3237.0   30.0  ...   15.0   14.0   14.0     71.0
3  gpj3qKVlP0FZb85kyh64    1.0  16583.0  294.0  ...    5.0    1.0    0.0   2794.0
4  dRAZE56pjBH8JwFnx9Uh    9.0   8345.0  137.0  ...   14.0    7.0    6.0   1146.0

[5 rows x 2202 columns]

In [ ]:
df.shape

(6500, 2202)

In [ ]:
###  -------***************----------------------------**************------------------------------------************---------------
# Delete all the byte files
!rm -r -f bytefiles/

### Split data into Train, Test and CV

In [ ]:
X = df.drop(['ID', 'Class'], axis = 1)
y = df['Class']
print(X.shape)
print(y.shape)

(6500, 2200)
(6500,)


In [ ]:
X_train, X_test, y_train, y_test = train_test_split(X, y,stratify=y,test_size=0.20)
X_train, X_cv, y_train, y_cv = train_test_split(X_train, y_train,stratify=y_train,test_size=0.20)

In [ ]:
X_train.shape, y_train.shape

((4160, 2200), (4160,))

In [ ]:
print(X.shape)
print(y.shape)

(6500, 2200)
(6500,)


In [ ]:
def plot_confusion_matrix(test_y, predict_y):
    C = confusion_matrix(test_y, predict_y)
    print("Number of misclassified points ",(len(test_y)-np.trace(C))/len(test_y)*100)
    # C = 9,9 matrix, each cell (i,j) represents number of points of class i are predicted class j

    A =(((C.T)/(C.sum(axis=1))).T)
    #divid each element of the confusion matrix with the sum of elements in that column

    # C = [[1, 2],
    #     [3, 4]]
    # C.T = [[1, 3],
    #        [2, 4]]
    # C.sum(axis = 1)  axis=0 corresonds to columns and axis=1 corresponds to rows in two diamensional array
    # C.sum(axix =1) = [[3, 7]]
    # ((C.T)/(C.sum(axis=1))) = [[1/3, 3/7]
    #                           [2/3, 4/7]]

    # ((C.T)/(C.sum(axis=1))).T = [[1/3, 2/3]
    #                           [3/7, 4/7]]
    # sum of row elements = 1

    B =(C/C.sum(axis=0))
    #divid each element of the confusion matrix with the sum of elements in that row
    # C = [[1, 2],
    #     [3, 4]]
    # C.sum(axis = 0)  axis=0 corresonds to columns and axis=1 corresponds to rows in two diamensional array
    # C.sum(axix =0) = [[4, 6]]
    # (C/C.sum(axis=0)) = [[1/4, 2/6],
    #                      [3/4, 4/6]]

    labels = [1,2,3,4,5,6,7,8,9]
    cmap=sns.light_palette("green")
    # representing A in heatmap format
    print("-"*50, "Confusion matrix", "-"*50)
    plt.figure(figsize=(10,5))
    sns.heatmap(C, annot=True, cmap=cmap, fmt=".3f", xticklabels=labels, yticklabels=labels)
    plt.xlabel('Predicted Class')
    plt.ylabel('Original Class')
    plt.show()

    print("-"*50, "Precision matrix", "-"*50)
    plt.figure(figsize=(10,5))
    sns.heatmap(B, annot=True, cmap=cmap, fmt=".3f", xticklabels=labels, yticklabels=labels)
    plt.xlabel('Predicted Class')
    plt.ylabel('Original Class')
    plt.show()
    print("Sum of columns in precision matrix",B.sum(axis=0))

    # representing B in heatmap format
    print("-"*50, "Recall matrix"    , "-"*50)
    plt.figure(figsize=(10,5))
    sns.heatmap(A, annot=True, cmap=cmap, fmt=".3f", xticklabels=labels, yticklabels=labels)
    plt.xlabel('Predicted Class')
    plt.ylabel('Original Class')
    plt.show()
    print("Sum of rows in precision matrix",A.sum(axis=1))

## Machine Learning Models on Bigram of 'bytefiles'

### Random Models

In [ ]:
# we need to generate 9 numbers and the sum of numbers should be 1
# one solution is to genarate 9 numbers and divide each of the numbers by their sum
# ref: https://stackoverflow.com/a/18662466/4084039

test_data_len = X_test.shape[0]
cv_data_len = X_cv.shape[0]

# we create a output array that has exactly same size as the CV data
cv_predicted_y = np.zeros((cv_data_len,9))
for i in tqdm(range(cv_data_len)):
    rand_probs = np.random.rand(1,9)
    cv_predicted_y[i] = ((rand_probs/sum(sum(rand_probs)))[0])
print("Log loss on Cross Validation Data using Random Model",log_loss(y_cv,cv_predicted_y, eps=1e-15))


# Test-Set error.
#we create a output array that has exactly same as the test data
test_predicted_y = np.zeros((test_data_len,9))
for i in range(test_data_len):
    rand_probs = np.random.rand(1,9)
    test_predicted_y[i] = ((rand_probs/sum(sum(rand_probs)))[0])
print("Log loss on Test Data using Random Model",log_loss(y_test,test_predicted_y, eps=1e-15))

predicted_y =np.argmax(test_predicted_y, axis=1)
plot_confusion_matrix(y_test, predicted_y+1)

100%|██████████| 1040/1040 [00:00<00:00, 49674.61it/s]

Log loss on Cross Validation Data using Random Model 2.5404696408424043
Log loss on Test Data using Random Model 2.4766882929640976
Number of misclassified points  87.46153846153845
-------------------------------------------------- Confusion matrix --------------------------------------------------


<IPython.core.display.Javascript object>

-------------------------------------------------- Precision matrix --------------------------------------------------


<IPython.core.display.Javascript object>

Sum of columns in precision matrix [1. 1. 1. 1. 1. 1. 1. 1. 1.]
-------------------------------------------------- Recall matrix --------------------------------------------------


<IPython.core.display.Javascript object>

Sum of rows in precision matrix [1. 1. 1. 1. 1. 1. 1. 1. 1.]


## K Nearest Neighbour Classification

In [ ]:
# find more about KNeighborsClassifier() here http://scikit-learn.org/stable/modules/generated/sklearn.neighbors.KNeighborsClassifier.html
# -------------------------
# default parameter
# KNeighborsClassifier(n_neighbors=5, weights=’uniform’, algorithm=’auto’, leaf_size=30, p=2,
# metric=’minkowski’, metric_params=None, n_jobs=1, **kwargs)

# methods of
# fit(X, y) : Fit the model using X as training data and y as target values
# predict(X):Predict the class labels for the provided data
# predict_proba(X):Return probability estimates for the test data X.
#-------------------------------------
# video link: https://www.appliedaicourse.com/course/applied-ai-course-online/lessons/k-nearest-neighbors-geometric-intuition-with-a-toy-example-1/
#-------------------------------------


# find more about CalibratedClassifierCV here at http://scikit-learn.org/stable/modules/generated/sklearn.calibration.CalibratedClassifierCV.html
# ----------------------------
# default paramters
# sklearn.calibration.CalibratedClassifierCV(base_estimator=None, method=’sigmoid’, cv=3)
#
# some of the methods of CalibratedClassifierCV()
# fit(X, y[, sample_weight])	Fit the calibrated model
# get_params([deep])	Get parameters for this estimator.
# predict(X)	Predict the target of new samples.
# predict_proba(X)	Posterior probabilities of classification
#-------------------------------------
# video link:
#-------------------------------------

alpha = [x for x in range(1, 15, 2)]
cv_log_error_array=[]
for i in tqdm(alpha):
    k_cfl=KNeighborsClassifier(n_neighbors=i)
    k_cfl.fit(X_train,y_train)
    sig_clf = CalibratedClassifierCV(k_cfl, method="sigmoid")
    sig_clf.fit(X_train, y_train)
    predict_y = sig_clf.predict_proba(X_cv)
    cv_log_error_array.append(log_loss(y_cv, predict_y, labels=k_cfl.classes_, eps=1e-15))

for i in range(len(cv_log_error_array)):
    print ('log_loss for k = ',alpha[i],'is',cv_log_error_array[i])

best_alpha = np.argmin(cv_log_error_array)

fig, ax = plt.subplots()
ax.plot(alpha, cv_log_error_array,c='g')
for i, txt in enumerate(np.round(cv_log_error_array,3)):
    ax.annotate((alpha[i],np.round(txt,3)), (alpha[i],cv_log_error_array[i]))
plt.grid()
plt.title("Cross Validation Error for each alpha")
plt.xlabel("Alpha i's")
plt.ylabel("Error measure")
plt.show()

k_cfl=KNeighborsClassifier(n_neighbors=alpha[best_alpha])
k_cfl.fit(X_train,y_train)
sig_clf = CalibratedClassifierCV(k_cfl, method="sigmoid")
sig_clf.fit(X_train, y_train)

predict_y = sig_clf.predict_proba(X_train)
print ('For values of best alpha = ', alpha[best_alpha], "The train log loss is:",log_loss(y_train, predict_y))
predict_y = sig_clf.predict_proba(X_cv)
print('For values of best alpha = ', alpha[best_alpha], "The cross validation log loss is:",log_loss(y_cv, predict_y))
predict_y = sig_clf.predict_proba(X_test)
print('For values of best alpha = ', alpha[best_alpha], "The test log loss is:",log_loss(y_test, predict_y))
plot_confusion_matrix(y_test, sig_clf.predict(X_test))

100%|██████████| 7/7 [04:31<00:00, 38.81s/it]

log_loss for k =  1 is 0.3767287125862504
log_loss for k =  3 is 0.35455472479714295
log_loss for k =  5 is 0.38274864205315995
log_loss for k =  7 is 0.40401052736974197
log_loss for k =  9 is 0.4283967923433955
log_loss for k =  11 is 0.44905877215632245
log_loss for k =  13 is 0.46797387232031407


<IPython.core.display.Javascript object>

For values of best alpha =  3 The train log loss is: 0.21238863640847816
For values of best alpha =  3 The cross validation log loss is: 0.35455472479714295
For values of best alpha =  3 The test log loss is: 0.35775714947347864
Number of misclassified points  9.076923076923077
-------------------------------------------------- Confusion matrix --------------------------------------------------


<IPython.core.display.Javascript object>

-------------------------------------------------- Precision matrix --------------------------------------------------


<IPython.core.display.Javascript object>

Sum of columns in precision matrix [1. 1. 1. 1. 1. 1. 1. 1. 1.]
-------------------------------------------------- Recall matrix --------------------------------------------------


<IPython.core.display.Javascript object>

Sum of rows in precision matrix [1. 1. 1. 1. 1. 1. 1. 1. 1.]


### Logistic Regression

In [ ]:
# read more about SGDClassifier() at http://scikit-learn.org/stable/modules/generated/sklearn.linear_model.SGDClassifier.html
# ------------------------------
# default parameters
# SGDClassifier(loss=’hinge’, penalty=’l2’, alpha=0.0001, l1_ratio=0.15, fit_intercept=True, max_iter=None, tol=None,
# shuffle=True, verbose=0, epsilon=0.1, n_jobs=1, random_state=None, learning_rate=’optimal’, eta0=0.0, power_t=0.5,
# class_weight=None, warm_start=False, average=False, n_iter=None)

# some of methods
# fit(X, y[, coef_init, intercept_init, …])	Fit linear model with Stochastic Gradient Descent.
# predict(X)	Predict class labels for samples in X.

#-------------------------------
# video link: https://www.appliedaicourse.com/course/applied-ai-course-online/lessons/geometric-intuition-1/
#------------------------------

alpha = [10 ** x for x in range(-5, 4)]
cv_log_error_array=[]
for i in tqdm(alpha):
    logisticR=LogisticRegression(penalty='l2',C=i,class_weight='balanced')
    logisticR.fit(X_train,y_train)
    sig_clf = CalibratedClassifierCV(logisticR, method="sigmoid")
    sig_clf.fit(X_train, y_train)
    predict_y = sig_clf.predict_proba(X_cv)
    cv_log_error_array.append(log_loss(y_cv, predict_y, labels=logisticR.classes_, eps=1e-15))

for i in range(len(cv_log_error_array)):
    print ('log_loss for c = ',alpha[i],'is',cv_log_error_array[i])

best_alpha = np.argmin(cv_log_error_array)

fig, ax = plt.subplots()
ax.plot(alpha, cv_log_error_array,c='g')
for i, txt in enumerate(np.round(cv_log_error_array,3)):
    ax.annotate((alpha[i],np.round(txt,3)), (alpha[i],cv_log_error_array[i]))
plt.grid()
plt.title("Cross Validation Error for each alpha")
plt.xlabel("Alpha i's")
plt.ylabel("Error measure")
plt.show()

logisticR=LogisticRegression(penalty='l2',C=alpha[best_alpha],class_weight='balanced')
logisticR.fit(X_train,y_train)
sig_clf = CalibratedClassifierCV(logisticR, method="sigmoid")
sig_clf.fit(X_train, y_train)
pred_y=sig_clf.predict(X_test)

print('Best alpha is :- ', alpha[best_alpha])
predict_y = sig_clf.predict_proba(X_train)
print ('log loss for train data',log_loss(y_train, predict_y, labels=logisticR.classes_, eps=1e-15))
predict_y = sig_clf.predict_proba(X_cv)
print ('log loss for cv data',log_loss(y_cv, predict_y, labels=logisticR.classes_, eps=1e-15))
predict_y = sig_clf.predict_proba(X_test)
print ('log loss for test data',log_loss(y_test, predict_y, labels=logisticR.classes_, eps=1e-15))
plot_confusion_matrix(y_test, sig_clf.predict(X_test))

100%|██████████| 9/9 [09:42<00:00, 64.76s/it]

log_loss for c =  1e-05 is 1.3379805137448015
log_loss for c =  0.0001 is 1.3260330366055921
log_loss for c =  0.001 is 1.3369754913639396
log_loss for c =  0.01 is 1.333912965798054
log_loss for c =  0.1 is 1.3182722043988746
log_loss for c =  1 is 1.3185233204188422
log_loss for c =  10 is 1.3124900809368472
log_loss for c =  100 is 1.323415089383854
log_loss for c =  1000 is 1.3150256782591319


<IPython.core.display.Javascript object>

Best alpha is :-  10
log loss for train data 1.3093925313962271
log loss for cv data 1.3124900809368472
log loss for test data 1.3247618469124827
Number of misclassified points  36.46153846153846
-------------------------------------------------- Confusion matrix --------------------------------------------------


<IPython.core.display.Javascript object>

-------------------------------------------------- Precision matrix --------------------------------------------------


<IPython.core.display.Javascript object>

Sum of columns in precision matrix [ 1.  1.  1. nan nan  1. nan nan  1.]
-------------------------------------------------- Recall matrix --------------------------------------------------


<IPython.core.display.Javascript object>

Sum of rows in precision matrix [1. 1. 1. 1. 1. 1. 1. 1. 1.]


### Random Forest Classifier on Bigram of 'bytefiles'

In [ ]:
# --------------------------------
# default parameters
# sklearn.ensemble.RandomForestClassifier(n_estimators=10, criterion=’gini’, max_depth=None, min_samples_split=2,
# min_samples_leaf=1, min_weight_fraction_leaf=0.0, max_features=’auto’, max_leaf_nodes=None, min_impurity_decrease=0.0,
# min_impurity_split=None, bootstrap=True, oob_score=False, n_jobs=1, random_state=None, verbose=0, warm_start=False,
# class_weight=None)

# Some of methods of RandomForestClassifier()
# fit(X, y, [sample_weight])	Fit the SVM model according to the given training data.
# predict(X)	Perform classification on samples in X.
# predict_proba (X)	Perform classification on samples in X.

# some of attributes of  RandomForestClassifier()
# feature_importances_ : array of shape = [n_features]
# The feature importances (the higher, the more important the feature).

# --------------------------------
# video link: https://www.appliedaicourse.com/course/applied-ai-course-online/lessons/random-forest-and-their-construction-2/
# --------------------------------

alpha=[10,50,100,500,1000,2000,3000]
cv_log_error_array=[]
train_log_error_array=[]
from sklearn.ensemble import RandomForestClassifier
for i in tqdm(alpha):
    r_cfl=RandomForestClassifier(n_estimators=i,random_state=42,n_jobs=-1)
    r_cfl.fit(X_train,y_train)
    sig_clf = CalibratedClassifierCV(r_cfl, method="sigmoid")
    sig_clf.fit(X_train, y_train)
    predict_y = sig_clf.predict_proba(X_cv)
    cv_log_error_array.append(log_loss(y_cv, predict_y, labels=r_cfl.classes_, eps=1e-15))

for i in range(len(cv_log_error_array)):
    print ('log_loss for c = ',alpha[i],'is',cv_log_error_array[i])


best_alpha = np.argmin(cv_log_error_array)

fig, ax = plt.subplots()
ax.plot(alpha, cv_log_error_array,c='g')
for i, txt in enumerate(np.round(cv_log_error_array,3)):
    ax.annotate((alpha[i],np.round(txt,3)), (alpha[i],cv_log_error_array[i]))
plt.grid()
plt.title("Cross Validation Error for each alpha")
plt.xlabel("Alpha i's")
plt.ylabel("Error measure")
plt.show()


r_cfl=RandomForestClassifier(n_estimators=alpha[best_alpha],random_state=42,n_jobs=-1)
r_cfl.fit(X_train,y_train)
sig_clf = CalibratedClassifierCV(r_cfl, method="sigmoid")
sig_clf.fit(X_train, y_train)

predict_y = sig_clf.predict_proba(X_train)
print('For values of best alpha = ', alpha[best_alpha], "The train log loss is:",log_loss(y_train, predict_y))
predict_y = sig_clf.predict_proba(X_cv)
print('For values of best alpha = ', alpha[best_alpha], "The cross validation log loss is:",log_loss(y_cv, predict_y))
predict_y = sig_clf.predict_proba(X_test)
print('For values of best alpha = ', alpha[best_alpha], "The test log loss is:",log_loss(y_test, predict_y))
plot_confusion_matrix(y_test, sig_clf.predict(X_test))

100%|██████████| 7/7 [19:38<00:00, 168.37s/it]

log_loss for c =  10 is 0.08495923710135962
log_loss for c =  50 is 0.0671953855143941
log_loss for c =  100 is 0.06450556964896938
log_loss for c =  500 is 0.06760136243878719
log_loss for c =  1000 is 0.06856573549054765
log_loss for c =  2000 is 0.0684598752488742
log_loss for c =  3000 is 0.06818482519218806


<IPython.core.display.Javascript object>

For values of best alpha =  100 The train log loss is: 0.026892172036837254
For values of best alpha =  100 The cross validation log loss is: 0.06450556964896938
For values of best alpha =  100 The test log loss is: 0.06875995634878876
Number of misclassified points  1.5384615384615385
-------------------------------------------------- Confusion matrix --------------------------------------------------


<IPython.core.display.Javascript object>

-------------------------------------------------- Precision matrix --------------------------------------------------


<IPython.core.display.Javascript object>

Sum of columns in precision matrix [1. 1. 1. 1. 1. 1. 1. 1. 1.]
-------------------------------------------------- Recall matrix --------------------------------------------------


<IPython.core.display.Javascript object>

Sum of rows in precision matrix [1. 1. 1. 1. 1. 1. 1. 1. 1.]


### Xgboost Classifier on Bigram of 'bytefiles


In [ ]:
# Training a hyper-parameter tuned Xg-Boost regressor on our train data

# find more about XGBClassifier function here http://xgboost.readthedocs.io/en/latest/python/python_api.html?#xgboost.XGBClassifier
# -------------------------
# default paramters
# class xgboost.XGBClassifier(max_depth=3, learning_rate=0.1, n_estimators=100, silent=True,
# objective='binary:logistic', booster='gbtree', n_jobs=1, nthread=None, gamma=0, min_child_weight=1,
# max_delta_step=0, subsample=1, colsample_bytree=1, colsample_bylevel=1, reg_alpha=0, reg_lambda=1,
# scale_pos_weight=1, base_score=0.5, random_state=0, seed=None, missing=None, **kwargs)

# some of methods of RandomForestRegressor()
# fit(X, y, sample_weight=None, eval_set=None, eval_metric=None, early_stopping_rounds=None, verbose=True, xgb_model=None)
# get_params([deep])	Get parameters for this estimator.
# predict(data, output_margin=False, ntree_limit=0) : Predict with data. NOTE: This function is not thread safe.
# get_score(importance_type='weight') -> get the feature importance
# -----------------------
# video link1: https://www.appliedaicourse.com/course/applied-ai-course-online/lessons/regression-using-decision-trees-2/
# video link2: https://www.appliedaicourse.com/course/applied-ai-course-online/lessons/what-are-ensembles/
# -----------------------

alpha=[10,50,100,500,1000,2000]
cv_log_error_array=[]
for i in tqdm(alpha):
    x_cfl=XGBClassifier(n_estimators=i,nthread=-1)
    x_cfl.fit(X_train,y_train)
    sig_clf = CalibratedClassifierCV(x_cfl, method="sigmoid")
    sig_clf.fit(X_train, y_train)
    predict_y = sig_clf.predict_proba(X_cv)
    cv_log_error_array.append(log_loss(y_cv, predict_y, labels=x_cfl.classes_, eps=1e-15))

for i in range(len(cv_log_error_array)):
    print ('log_loss for c = ',alpha[i],'is',cv_log_error_array[i])


best_alpha = np.argmin(cv_log_error_array)

fig, ax = plt.subplots()
ax.plot(alpha, cv_log_error_array,c='g')
for i, txt in enumerate(np.round(cv_log_error_array,3)):
    ax.annotate((alpha[i],np.round(txt,3)), (alpha[i],cv_log_error_array[i]))
plt.grid()
plt.title("Cross Validation Error for each alpha")
plt.xlabel("Alpha i's")
plt.ylabel("Error measure")
plt.show()

x_cfl=XGBClassifier(n_estimators=alpha[best_alpha],nthread=-1)
x_cfl.fit(X_train,y_train)
sig_clf = CalibratedClassifierCV(x_cfl, method="sigmoid")
sig_clf.fit(X_train, y_train)

predict_y = sig_clf.predict_proba(X_train)
print ('For values of best alpha = ', alpha[best_alpha], "The train log loss is:",log_loss(y_train, predict_y))
predict_y = sig_clf.predict_proba(X_cv)
print('For values of best alpha = ', alpha[best_alpha], "The cross validation log loss is:",log_loss(y_cv, predict_y))
predict_y = sig_clf.predict_proba(X_test)
print('For values of best alpha = ', alpha[best_alpha], "The test log loss is:",log_loss(y_test, predict_y))
plot_confusion_matrix(y_test, sig_clf.predict(X_test))

100%|██████████| 6/6 [3:51:59<00:00, 2319.86s/it]

log_loss for c =  10 is 0.13239415559985604
log_loss for c =  50 is 0.07346678579728728
log_loss for c =  100 is 0.06419113873712101
log_loss for c =  500 is 0.06306105746729998
log_loss for c =  1000 is 0.06293400405829423
log_loss for c =  2000 is 0.0629339054647781


<IPython.core.display.Javascript object>

For values of best alpha =  2000 The train log loss is: 0.02435149863779557
For values of best alpha =  2000 The cross validation log loss is: 0.0629339054647781
For values of best alpha =  2000 The test log loss is: 0.04982917757541673
Number of misclassified points  0.9230769230769231
-------------------------------------------------- Confusion matrix --------------------------------------------------


<IPython.core.display.Javascript object>

-------------------------------------------------- Precision matrix --------------------------------------------------


<IPython.core.display.Javascript object>

Sum of columns in precision matrix [1. 1. 1. 1. 1. 1. 1. 1. 1.]
-------------------------------------------------- Recall matrix --------------------------------------------------


<IPython.core.display.Javascript object>

Sum of rows in precision matrix [1. 1. 1. 1. 1. 1. 1. 1. 1.]


### Xgboost Classifier (best hyperparameter) on Bigram of 'bytefiles'


In [ ]:
# https://www.analyticsvidhya.com/blog/2016/03/complete-guide-parameter-tuning-xgboost-with-codes-python/
import time as tm
start_time = tm.time()
x_cfl=XGBClassifier()

prams={
    'learning_rate':[0.01,0.03,0.05,0.1,0.15,0.2],
     'n_estimators':[100,200,500,1000,2000],
     'max_depth':[3,5,10],
    'colsample_bytree':[0.1,0.3,0.5,1],
    'subsample':[0.1,0.3,0.5,1]
}
random_cfl1=RandomizedSearchCV(x_cfl,param_distributions=prams,verbose=10,n_jobs=-1,)
random_cfl1.fit(X_train,y_train)
print('Time taken is :- ', (tm.time() - start_time)/ 3600, 'hours')

Fitting 5 folds for each of 10 candidates, totalling 50 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 2 concurrent workers.
[Parallel(n_jobs=-1)]: Done   1 tasks      | elapsed: 22.2min
[Parallel(n_jobs=-1)]: Done   4 tasks      | elapsed: 44.8min
[Parallel(n_jobs=-1)]: Done   9 tasks      | elapsed: 113.2min
[Parallel(n_jobs=-1)]: Done  14 tasks      | elapsed: 187.4min
[Parallel(n_jobs=-1)]: Done  21 tasks      | elapsed: 235.1min
[Parallel(n_jobs=-1)]: Done  28 tasks      | elapsed: 264.7min
[Parallel(n_jobs=-1)]: Done  37 tasks      | elapsed: 286.5min
[Parallel(n_jobs=-1)]: Done  46 tasks      | elapsed: 471.2min
[Parallel(n_jobs=-1)]: Done  50 out of  50 | elapsed: 529.8min finished


Time taken is :-  9.190305932561557 hours


In [ ]:
print(random_cfl1.best_params_)

{'subsample': 0.5, 'n_estimators': 1000, 'max_depth': 3, 'learning_rate': 0.15, 'colsample_bytree': 1}


In [ ]:
# Training a hyper-parameter tuned Xg-Boost regressor on our train data

# find more about XGBClassifier function here http://xgboost.readthedocs.io/en/latest/python/python_api.html?#xgboost.XGBClassifier
# -------------------------
# default paramters
# class xgboost.XGBClassifier(max_depth=3, learning_rate=0.1, n_estimators=100, silent=True,
# objective='binary:logistic', booster='gbtree', n_jobs=1, nthread=None, gamma=0, min_child_weight=1,
# max_delta_step=0, subsample=1, colsample_bytree=1, colsample_bylevel=1, reg_alpha=0, reg_lambda=1,
# scale_pos_weight=1, base_score=0.5, random_state=0, seed=None, missing=None, **kwargs)

# some of methods of RandomForestRegressor()
# fit(X, y, sample_weight=None, eval_set=None, eval_metric=None, early_stopping_rounds=None, verbose=True, xgb_model=None)
# get_params([deep])	Get parameters for this estimator.
# predict(data, output_margin=False, ntree_limit=0) : Predict with data. NOTE: This function is not thread safe.
# get_score(importance_type='weight') -> get the feature importance
# -----------------------
# video link2: https://www.appliedaicourse.com/course/applied-ai-course-online/lessons/what-are-ensembles/
# -----------------------

# x_cfl=XGBClassifier(n_estimators=2000, learning_rate=0.05, colsample_bytree=1, max_depth=3)
x_cfl=XGBClassifier(n_estimators=1000, learning_rate=0.15, colsample_bytree=1, max_depth=3)
x_cfl.fit(X_train,y_train)
c_cfl=CalibratedClassifierCV(x_cfl,method='sigmoid')
c_cfl.fit(X_train,y_train)

predict_y = c_cfl.predict_proba(X_train)
print ('train loss',log_loss(y_train, predict_y))
predict_y = c_cfl.predict_proba(X_cv)
print ('cv loss',log_loss(y_cv, predict_y))
predict_y = c_cfl.predict_proba(X_test)
print ('test loss',log_loss(y_test, predict_y))
plot_confusion_matrix(y_test,sig_clf.predict(X_test))

train loss 0.02233276307823185
cv loss 0.06872953495905615
test loss 0.07952372511237249
Number of misclassified points  36.46153846153846
-------------------------------------------------- Confusion matrix --------------------------------------------------


<IPython.core.display.Javascript object>

-------------------------------------------------- Precision matrix --------------------------------------------------


<IPython.core.display.Javascript object>

Sum of columns in precision matrix [ 1.  1.  1. nan nan  1. nan nan  1.]
-------------------------------------------------- Recall matrix --------------------------------------------------


<IPython.core.display.Javascript object>

Sum of rows in precision matrix [1. 1. 1. 1. 1. 1. 1. 1. 1.]


In [ ]:
from prettytable import PrettyTable

table = PrettyTable()
table.field_names  = ['Model', 'Best Hyper Parameter', 'Train Log Loss', 'CV Log Loss', 'Test Log Loss', 'Number of Misclassified Points']
# table.add_row(['Random Models', 000, 0000000000000, 2.5047251297144077, 2.4618977024349054, 1.88.36538461538461])
table.add_row(['knn  Classifier', 3, 0.21238863640847816, 0.35455472479714295, 0.35775714947347864, 9.076923076923077])
table.add_row(['Logistic Regression ', 10, 1.3093925313962271, 1.3124900809368472, 1.3247618469124827, 36.46153846153846])

table.add_row(['Random Forest Classifier', 100, 0.026892172036837254, 0.06450556964896938, 0.06875995634878876, 1.5384615384615385])
table.add_row(['XgBoost Classifier', 2000, 0.02435149863779557, 0.0629339054647781, 0.04982917757541673, 0.9230769230769231])
table.add_row(['XgBoost Classifier with Best Hyper Parameter', 1000, 0.02233276307823185, 0.06872953495905615, 0.07952372511237249, 36.46153846153846])


print(table)


+----------------------------------------------+----------------------+----------------------+---------------------+---------------------+--------------------------------+
|                    Model                     | Best Hyper Parameter |    Train Log Loss    |     CV Log Loss     |    Test Log Loss    | Number of Misclassified Points |
+----------------------------------------------+----------------------+----------------------+---------------------+---------------------+--------------------------------+
|               knn  Classifier                |          3           | 0.21238863640847816  | 0.35455472479714295 | 0.35775714947347864 |       9.076923076923077        |
|             Logistic Regression              |          10          |  1.3093925313962271  |  1.3124900809368472 |  1.3247618469124827 |       36.46153846153846        |
|           Random Forest Classifier           |         100          | 0.026892172036837254 | 0.06450556964896938 | 0.06875995634878876 |  

In [ ]:
# you can extract only one set of files
# first try changing the run time to GPU so that you can get more hard disk
# download only train.7z file, if you have dowloaded all the files from the competiion you can remove other files except train.7z
# then as shown in the above cell you can extract only the byte files
# after you extract byte files
# for every bytefile:
#   create bigrams from that files, it should be stright forward for you,
#   you can reuse the code in your tfidf assignment or you can use the tfidf vectorizer with fixed vocabulary
#   so after the computing of the bigrams it will be a 1*vocab size sparse matrix
#   delete the file extracted byte file

# you need to concatinate all the sparse matrices, which makes the final matrix of size (number_of_bytefiles, len_vocab)

# you can do the same thing for the asm files also, after you the above for loop, all the byte files might have been removed
# extract only asm files
# for every asm file:
#   create pixel features, check the reference we have given
#   so after the computing of the pixel features it will be a 1*len_pixel_values a dense matrix
#   delete the file extracting asm file

In [ ]:
# Store both the sparse matrix, which holds the bigrams and the the dense matrix which holds the pixel matrix into pickle files so that you can reuse them later

# if you can identify each row of the matrix by a unique file name, that might be help you in train test split separation


In [ ]:
# # Multiprocessing image process generation across multiple cores in a CPU
# def read_image_process(files):
#     # files = os.listdir('asmbatch')
#     file1 = open("asmimagefirst.csv", "w+")
#     for i, filename in enumerate(files):
#         if(i%20==0):
#             print('First process-progress', i)
#         f = open('asmbatch/'+filename,'rb')
#         ln = os.path.getsize('asmbatch/'+filename)
#         width = 256
#         rem = ln%width
#         a = array.array("B")
#         a.fromfile(f, ln-rem)
#         f.close()
#         g = np.resize(a, (int(len(a)/width),width))
#         g = np.uint8(g)
#         # As suggested by 'say no to overfitting'
#         g = np.resize(g, (80,))
#         c = ','.join([str(s) for s in g])
#         f2 = filename.split('.')[0]
#         file1.write(f2+",")
#         file1.write(c)
#         file1.write('\n')
#     file1.close()

In [ ]:
# count=0
# batch=0
# time_taken=[]
# start=datetime.now()
# for file in asm_file_name:
#   # start=datetime.now()
#   !7z e train.7z -o/content/asmbatch *$file -r
#   count+=1
#   #Add your code here
#   if(batch == 10):
#     print('Batch 10 breaking')
#     break
#   if(count==10):
#       count=0
#       batch+=1
#       !rm -r -f asmbatch/
#       !mkdir asmbatch
#       end=datetime.now()
#       print('*'*50)
#       print('end, start',end,start)
#       difference=end-start
#       start=datetime.now()
#       time_taken.append('Time taken for the batch {} of ASM files is {}'.format(batch,difference))
#       print('Time taken for the batch {} of ASM files is {}'.format(batch,difference))

### Feature extraction for unigram bytefiles

In [ ]:
unigram_byte_features = pd.read_csv('/content/drive/MyDrive/16. Microsoft Malware Detection/result_with_size.csv').drop('Unnamed: 0', axis=1)
unigram_byte_features.head()

ID       0     1     2  ...     ff     ??      size  Class
0  01azqd4InC7m9JpocGv5  601905  3905  2816  ...   5753   1824  4.234863      9
1  01IsoiSMh5gxyDYTl4CB   39755  8337  7249  ...  54902   8588  5.538818      2
2  01jsnpXSAlgw6aPeDxrU   93506  9542  2568  ...  49144    468  3.887939      9
3  01kcPWA9K2BOxQeS5Rju   21091  1213   726  ...   7998  13940  0.574219      1
4  01SuzwMJEIXsK7A8dQbl   19764   710   302  ...   2199   9008  0.370850      8

[5 rows x 260 columns]

In [ ]:
unigram_byte_features.columns

Index(['ID', '0', '1', '2', '3', '4', '5', '6', '7', '8',
       ...
       'f9', 'fa', 'fb', 'fc', 'fd', 'fe', 'ff', '??', 'size', 'Class'],
      dtype='object', length=260)

### Feature extraction for unigram asmfiles

In [ ]:
asmoutputfile = pd.read_csv('/content/drive/MyDrive/16. Microsoft Malware Detection/asmoutputfile.csv')
asmoutputfile.head()

ID  HEADER:  .text:  .Pav:  ...  edi  ebp  esp  eip
0  01kcPWA9K2BOxQeS5Rju       19     744      0  ...    0   17   48   29
1  1E93CpP60RHFNiT5Qfvn       17     838      0  ...    0   14    0   20
2  3ekVow2ajZHbTnBcsDfX       17     427      0  ...    0   11    0    9
3  3X2nY7iQaPBIWDrAZqJe       17     227      0  ...    0    8    0    6
4  46OZzdsSKDCFV8h7XWxf       17     402      0  ...    0   11    0   11

[5 rows x 52 columns]

In [ ]:
asm_with_size = pd.read_csv('/content/drive/MyDrive/16. Microsoft Malware Detection/asm_with_size.csv').drop('Unnamed: 0', axis=1)
asm_with_size.head()

ID   size_asm  Class
0  01azqd4InC7m9JpocGv5  56.229886      9
1  01IsoiSMh5gxyDYTl4CB  13.999378      2
2  01jsnpXSAlgw6aPeDxrU   8.507785      9
3  01kcPWA9K2BOxQeS5Rju   0.078190      1
4  01SuzwMJEIXsK7A8dQbl   0.996723      8

In [ ]:
asm_unigrams = pd.merge(asmoutputfile, asm_with_size.drop(['size_asm'], axis=1), on='ID')
asm_unigrams.head()

ID  HEADER:  .text:  .Pav:  ...  ebp  esp  eip  Class
0  01kcPWA9K2BOxQeS5Rju       19     744      0  ...   17   48   29      1
1  1E93CpP60RHFNiT5Qfvn       17     838      0  ...   14    0   20      1
2  3ekVow2ajZHbTnBcsDfX       17     427      0  ...   11    0    9      1
3  3X2nY7iQaPBIWDrAZqJe       17     227      0  ...    8    0    6      1
4  46OZzdsSKDCFV8h7XWxf       17     402      0  ...   11    0   11      1

[5 rows x 53 columns]

In [ ]:
asm_unigrams.shape

(10868, 53)

In [ ]:
print(asm_unigrams.columns)

Index(['ID', 'HEADER:', '.text:', '.Pav:', '.idata:', '.data:', '.bss:',
       '.rdata:', '.edata:', '.rsrc:', '.tls:', '.reloc:', '.BSS:', '.CODE',
       'jmp', 'mov', 'retf', 'push', 'pop', 'xor', 'retn', 'nop', 'sub', 'inc',
       'dec', 'add', 'imul', 'xchg', 'or', 'shr', 'cmp', 'call', 'shl', 'ror',
       'rol', 'jnb', 'jz', 'rtn', 'lea', 'movzx', '.dll', 'std::', ':dword',
       'edx', 'esi', 'eax', 'ebx', 'ecx', 'edi', 'ebp', 'esp', 'eip', 'Class'],
      dtype='object')


### Merging byte unigrams and asm unigrams

In [ ]:
# result_x = pd.merge(result,result_asm.drop(['Class'], axis=1),on='ID', how='left')
unigram_asm_byte_features = pd.merge(unigram_byte_features.drop(['Class', 'size'], axis=1), asm_unigrams, on='ID', how='left')
unigram_asm_byte_features.head()

ID       0     1     2     3  ...  edi  ebp  esp  eip  Class
0  01azqd4InC7m9JpocGv5  601905  3905  2816  3832  ...    0   15   14  456      9
1  01IsoiSMh5gxyDYTl4CB   39755  8337  7249  7186  ...    0   24   22  227      2
2  01jsnpXSAlgw6aPeDxrU   93506  9542  2568  2438  ...    0   27    0  117      9
3  01kcPWA9K2BOxQeS5Rju   21091  1213   726   817  ...    0   17   48   29      1
4  01SuzwMJEIXsK7A8dQbl   19764   710   302   433  ...    0   15    0   76      8

[5 rows x 310 columns]

In [ ]:
unigram_asm_byte_features.shape

(10868, 310)

In [ ]:
unigram_asm_byte_features.dtypes

ID       object
0         int64
1         int64
2         int64
3         int64
          ...  
edi       int64
ebp       int64
esp       int64
eip       int64
Class     int64
Length: 310, dtype: object

In [ ]:
print(unigram_asm_byte_features.columns)

Index(['ID', '0', '1', '2', '3', '4', '5', '6', '7', '8',
       ...
       'edx', 'esi', 'eax', 'ebx', 'ecx', 'edi', 'ebp', 'esp', 'eip', 'Class'],
      dtype='object', length=310)


In [ ]:
prefixes = ['HEADER:','.text:','.Pav:','.idata:','.data:','.bss:','.rdata:','.edata:','.rsrc:','.tls:','.reloc:','.BSS:','.CODE']
opcodes = ['jmp', 'mov', 'retf', 'push', 'pop', 'xor', 'retn', 'nop', 'sub', 'inc', 'dec', 'add','imul', 'xchg', 'or', 'shr', 'cmp', 'call', 'shl', 'ror', 'rol', 'jnb','jz','rtn','lea','movzx']
keywords = ['.dll','std::',':dword']
registers=['edx','esi','eax','ebx','ecx','edi','ebp','esp','eip']
print(len(prefixes) + len(opcodes) + len(keywords) + len(registers))

51


### Merging byte unigram , asm unigrams, 2200_byte_bigrams

In [ ]:
# https://thispointer.com/pandas-merge-dataframes-on-specific-columns-or-on-index-in-python-part-2/
unigram_asm_byte_bigram_byte_features = pd.merge(df, unigram_asm_byte_features.drop(['Class'], axis=1), on='ID', how='left') #
print(unigram_asm_byte_bigram_byte_features.shape)
unigram_asm_byte_bigram_byte_features.head()

(6500, 2510)


ID  Class    00 00  00 01   00 02  ...  ecx  edi  ebp  esp  eip
0  5sLXK39w4fkSzAVi1Q6U    8.0  26269.0  209.0    95.0  ...   62    0   29    0  377
1  BAzLufVOT1dQk0yg9X8o    2.0  22910.0  721.0  1056.0  ...   64    0   10    0   80
2  e1oUMvCJ5rNWFnLdPglK    3.0   3237.0   30.0    18.0  ...  225    0   12    0   39
3  gpj3qKVlP0FZb85kyh64    1.0  16583.0  294.0    71.0  ...  130    0   18    0  139
4  dRAZE56pjBH8JwFnx9Uh    9.0   8345.0  137.0    15.0  ...   82    0   21    0  104

[5 rows x 2510 columns]

In [ ]:
unigram_asm_byte_bigram_byte_features.shape

(6500, 2510)

In [ ]:
print(type(unigram_asm_byte_bigram_byte_features))

<class 'pandas.core.frame.DataFrame'>


In [ ]:
unigram_asm_byte_bigram_byte_features.dtypes

ID        object
Class    float64
00 00    float64
00 01    float64
00 02    float64
          ...   
ecx        int64
edi        int64
ebp        int64
esp        int64
eip        int64
Length: 2510, dtype: object

In [ ]:
# unigram_asm_byte_features = normalize()
# https://stackoverflow.com/questions/36814100/pandas-to-numeric-for-multiple-columns
# https://stackoverflow.com/questions/15891038/change-column-type-in-pandas
# unigram_asm_byte_features.drop(['ID'], axis=1).astype(float)

In [ ]:
# model_X = unigram_asm_byte_bigram_byte_features[unigram_asm_byte_bigram_byte_features.iloc[:2:2510]]
# model_y = unigram_asm_byte_bigram_byte_features[unigram_asm_byte_bigram_byte_features.iloc[:2]]
# print(model_X.shape)
# print(model_y.shape)

In [ ]:
model_X = unigram_asm_byte_bigram_byte_features.drop(['ID', 'Class'], axis = 1)
model_y = unigram_asm_byte_bigram_byte_features['Class']
print(model_X.shape)
print(model_y.shape)

(6500, 2508)
(6500,)


In [ ]:
# ***************************************************************************